In [2]:
import pandas as pd
import plotly.express as px
from pathlib import Path

In [6]:
root_dir = Path().absolute().parent
data_dir = root_dir / 'web-app/public/data'
data_dir.exists()

True

In [13]:
file_path = data_dir / 'consumption.csv'
df = pd.read_csv(file_path, parse_dates=['timestamp'], delimiter=',').set_index('timestamp')
df.plot(backend='plotly')

In [ ]:
file_path = data_dir / 'solar_data_southern_france.csv'
df = pd.read_csv(file_path, parse_dates=['timestamp']).set_index('timestamp')
df.plot(backend='plotly')

In [ ]:
df['production_kw'] = df['production_kw'] * 120
df.plot(backend='plotly')


In [19]:
file_path = data_dir / 'solar_data_southern_france.csv'
df = pd.read_csv(file_path, parse_dates=['timestamp'])
px.line(
    df,
    x='timestamp',
    y='production_kw',
    title='Graphique avec Lignes et Points (Markers)',
    markers=True  # <--- Ceci active les marqueurs
)


In [42]:
file_path = data_dir / 'solar_data_southern_france.csv'
df = pd.read_csv(file_path, parse_dates=['timestamp']).set_index('timestamp')
df['production_kw'] = df['production_kw'] * 200
df_hourly = df.resample('15min').mean()
df_hourly.to_csv(root_dir / 'web-app/public/data/solar_production_2.csv')
df_hourly.plot(backend='plotly')


In [41]:
file_path = data_dir / 'solar_data_southern_france.csv'
df = pd.read_csv(file_path, parse_dates=['timestamp']).set_index('timestamp')
df.plot(backend='plotly')


In [25]:
df_hourly = df.resample('15min').sum()
df_hourly.plot(backend='plotly')

In [ ]:
file_path = r'C:\Users\ltsawv5.LTSW2K\Documents\projects\perso\moonlight\data-fetcher\enedis_puissance_2024_20251213_194825.csv'
df = pd.read_csv(file_path, parse_dates=['horodate']).set_index('horodate')
df.plot(backend='plotly')

In [ ]:
import requests


In [ ]:
BASE_URL = "https://data.enedis.fr/api/explore/v2.1/catalog/datasets/bilan-electrique-demi-heure/records"
# Le nombre de lignes par requête est maintenant le nombre max par mois.
ROWS_PER_REQUEST = 31 * 48 * 2  # Environ 3000, 10000 est sûr.
TARGET_YEAR = 2024

In [ ]:
params = {
    # Filtre sur le mois et l'année
    "refine": f"horodate:2024/01",
    "order_by": "horodate",
    # "select": "horodate, injection_rte, soutirage_rte",
}
response = requests.get(BASE_URL, params=params, verify=False)
response

In [ ]:
data = response.json()
data['results']

In [ ]:
def show(file_path: str, time_index: str, value_column: str, nb_days: int = 3):
    try:
        df = pd.read_csv(
            file_path,
            sep=',',
            parse_dates=[time_index],
            index_col=time_index
        )
    except FileNotFoundError:
        print(f"Erreur : Le fichier '{file_path}' n'a pas été trouvé. Veuillez vérifier le chemin.")
        exit()
    start = df.index[0].normalize()
    end = start + pd.Timedelta(days=nb_days) - pd.Timedelta(minutes=1)
    df_reduced = df.loc[start:end]

    fig = px.line(
        df_reduced,
        x=df_reduced.index, # L'index (datetime) pour l'axe des x
        y=value_column,
        title='Puissance Solaire sur une Année',
        labels={'x': 'Date et Heure', value_column: 'Puissance Solaire (kW)'}
    )

    # 4. Ajuster la mise en page pour un meilleur affichage (optionnel)
    fig.update_xaxes(
        rangeslider_visible=True, # Ajoute un curseur de plage pour zoomer sur l'axe des x
        rangeselector=dict(
            buttons=list([
                dict(count=1, label="1m", step="month", stepmode="backward"),
                dict(count=6, label="6m", step="month", stepmode="backward"),
                dict(step="all")
            ])
        )
    )

    # 5. Afficher le graphique
    fig.show()      

In [ ]:
file_path = root_dir / 'data/solar_production.csv'
show(file_path, 'timestamp', 'production_kw', nb_days=3)


In [ ]:
file_path = root_dir / 'data/consumption.csv'
show(file_path, 'timestamp', 'consumption_kw', nb_days=3)


In [ ]:
# timestamp,production_kw

In [ ]:

# 2. Lire le fichier CSV avec pandas
#    - L'option `parse_dates=True` est cruciale pour que pandas reconnaisse la colonne 'datetime' comme des dates.
#    - `index_col='datetime'` rend la colonne datetime l'index du DataFrame, ce qui est souvent utile pour les séries temporelles.
try:
    df = pd.read_csv(
        file_path,
        sep=',',
        parse_dates=['timestamp'],
        index_col='timestamp'
    )
except FileNotFoundError:
    print(f"Erreur : Le fichier '{file_path}' n'a pas été trouvé. Veuillez vérifier le chemin.")
    exit()


In [ ]:
start = df.index[0].normalize()
end = start + pd.Timedelta(days=3) - pd.Timedelta(minutes=1)
df_reduced = df.loc[start:end]
df_reduced

In [ ]:

# 3. Créer le graphique de la série temporelle avec Plotly Express
#    - Plotly Express (px) rend la création de graphiques de base très simple.
#    - Nous utilisons `df.index` pour l'axe des x (les dates/heures) et la colonne 'power_kw' pour l'axe des y.
fig = px.line(
    df_reduced,
    x=df_reduced.index, # L'index (datetime) pour l'axe des x
    y='production_kw',
    title='Puissance Solaire sur une Année',
    labels={'x': 'Date et Heure', 'production_kw': 'Puissance Solaire (kW)'}
)

# 4. Ajuster la mise en page pour un meilleur affichage (optionnel)
fig.update_xaxes(
    rangeslider_visible=True, # Ajoute un curseur de plage pour zoomer sur l'axe des x
    rangeselector=dict(
        buttons=list([
            dict(count=1, label="1m", step="month", stepmode="backward"),
            dict(count=6, label="6m", step="month", stepmode="backward"),
            dict(step="all")
        ])
    )
)

# 5. Afficher le graphique
fig.show()